## Application



Goal : Gender and age classification


## Setup Monk

#### Download Monk

In [3]:
!git clone https://github.com/Tessellate-Imaging/monk_v1

Cloning into 'monk_v1'...
remote: Enumerating objects: 543, done.
remote: Counting objects: 100% (543/543), done.
remote: Compressing objects: 100% (363/363), done.
remote: Total 543 (delta 172), reused 523 (delta 162), pack-reused 0
Receiving objects: 100% (543/543), 4.43 MiB | 3.46 MiB/s, done.
Resolving deltas: 100% (172/172), done.


#### Setup dependencies

In [13]:
cd monk_v1

/content/monk_v1


In [15]:
!pip install -r installation/requirements_cu10.txt

     |████████████████████████████████| 81kB 2.6MB/s 
     |████████████████████████████████| 281.7MB 56kB/s 
     |████████████████████████████████| 540.1MB 34kB/s 
     |████████████████████████████████| 512kB 40.0MB/s 
     |████████████████████████████████| 748.9MB 23kB/s 
     |████████████████████████████████| 8.8MB 33.0MB/s 
     |████████████████████████████████| 3.1MB 28.2MB/s 
  Created wheel for gpustat: filename=gpustat-0.6.0-cp36-none-any.whl size=12620 sha256=dcf52ec86ec898668faf8b600bfa0565d27fd2f49bec4a66f7addd94d90f1e78
  Stored in directory: /root/.cache/pip/wheels/48/b4/d5/fb5b7f1d040f2ff20687e3bad6867d63155dbde5a7c10f4293
  Created wheel for GPUtil: filename=GPUtil-1.4.0-cp36-none-any.whl size=7410 sha256=9cd75660564235f1d0ee48262061e1c4e65849ea788d6c66bb576cce41944f53
  Stored in directory: /root/.cache/pip/wheels/3d/77/07/80562de4bb0786e5ea186911a2c831fdd0018bda69beab71fd
Successfully built gpustat GPUtil
ERROR: tensorflow 1.15.0 has requirement tensorboard<1.16.0

In [16]:
cd ..

/content


#### Import Monk

In [0]:
import os
import sys
sys.path.append("./monk_v1/monk");
import psutil
from pytorch_prototype import prototype

## Prepare Dataset

#### Download Dataset

In [18]:
!wget https://www.dropbox.com/s/3c34o03agjuydlg/age.zip

--2019-11-10 09:53:03--  https://www.dropbox.com/s/3c34o03agjuydlg/age.zip
Resolving www.dropbox.com (www.dropbox.com)... 162.125.82.1, 2620:100:6032:1::a27d:5201
Connecting to www.dropbox.com (www.dropbox.com)|162.125.82.1|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /s/raw/3c34o03agjuydlg/age.zip [following]
--2019-11-10 09:53:03--  https://www.dropbox.com/s/raw/3c34o03agjuydlg/age.zip
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uc34a16ac0873791deef5af6be72.dl.dropboxusercontent.com/cd/0/inline/AsE3zqIbGBJUNloY6GwdkW4YZvXtyO0x4HdMv5x9NyzRauZTcOBVyf8b5Y_0EbEBE_2cTQVKrnIjqJB9pfQo3UMM8ys_WduRYzvBuZIEZpt4Qkll1WVlrvmsMyI4S8Cxpn4/file# [following]
--2019-11-10 09:53:04--  https://uc34a16ac0873791deef5af6be72.dl.dropboxusercontent.com/cd/0/inline/AsE3zqIbGBJUNloY6GwdkW4YZvXtyO0x4HdMv5x9NyzRauZTcOBVyf8b5Y_0EbEBE_2cTQVKrnIjqJB9pfQo3UMM8ys_WduRYzvBuZIEZpt4Qkll1WVlrvmsMyI4S8

#### Extract Dataset

In [0]:
#!rm -rf age

In [20]:
%%capture
!unzip age.zip

Archive:  age.zip
   creating: age/
  inflating: __MACOSX/._age          
  inflating: age/.DS_Store           
  inflating: __MACOSX/age/._.DS_Store  
   creating: age/male/
  inflating: __MACOSX/age/._male     
   creating: age/female/
  inflating: __MACOSX/age/._female   
   creating: age/male/age_55_59/
  inflating: __MACOSX/age/male/._age_55_59  
   creating: age/male/age_30_34/
  inflating: __MACOSX/age/male/._age_30_34  
  inflating: age/male/.DS_Store      
  inflating: __MACOSX/age/male/._.DS_Store  
   creating: age/male/age_60_94/
  inflating: __MACOSX/age/male/._age_60_94  
   creating: age/male/age_25_29/
  inflating: __MACOSX/age/male/._age_25_29  
   creating: age/male/age_15_19/
  inflating: __MACOSX/age/male/._age_15_19  
   creating: age/male/age_40_44/
  inflating: __MACOSX/age/male/._age_40_44  
   creating: age/male/age_50_54/
  inflating: __MACOSX/age/male/._age_50_54  
   creating: age/male/age_35_39/
  inflating: __MACOSX/age/male/._age_35_39  
   creating: age/

#### Create Gender dataset

In [0]:
!mkdir gender
!mkdir gender/male
!mkdir gender/female

In [22]:
import glob
import shutil
from tqdm import tqdm


maleAgeList = glob.glob("./age/male/*")
femaleAgeList = glob.glob("./age/female/*")

for i in tqdm(maleAgeList):
  imageList = glob.glob(i + "/*.png")
  for j in imageList:
    outPath = "./gender/male/" + j.split('/')[-1]
    shutil.move(j,outPath)

for i in tqdm(femaleAgeList):
  imageList = glob.glob(i + "/*.jpg")
  for j in imageList:
    outPath = "./gender/female/" + j.split('/')[-1]
    shutil.move(j,outPath)


100%|██████████| 11/11 [00:00<00:00, 20.26it/s]


## Gender Classification Training

#### Create experiment

In [23]:
ptf = prototype(verbose=1);
ptf.Prototype("Gender_Classification", "exp-1");

Pytorch Version: 1.2.0

Experiment Details
    Project: Gender_Classification
    Experiment: exp-1
    Dir: /content/workspace/Gender_Classification/exp-1/



#### List Models to Choose from

In [24]:
ptf.List_Models()

Models List: 
    1. alexnet
    2. vgg11
    3. vgg11_bn
    4. vgg13
    5. vgg13_bn
    6. vgg16
    7. vgg16_bn
    8. vgg19
    9. vgg19_bn
    10. densenet121
    11. densenet161
    12. densenet169
    13. densenet201
    14. googlenet
    15. inception_v3
    16. resnet18
    17. resnet34
    18. resnet50
    19. resnet101
    20. resnet152
    21. resnext50_32x4d
    22. resnext101_32x8d
    23. shufflenet_v2_x0_5
    24. shufflenet_v2_x1_0, shufflenet_v2_x1_5
    25. shufflenet_v2_x2_0
    26. wide_resnet101_2
    27. wide_resnet50_2
    28. mnasnet0_5
    29. mnasnet0_75
    30. mnasnet1_0
    31. mnasnet1_3
    32. mobilenet_v2
    33. squeezenet1_0
    34. squeezenet1_1



#### Load Dataset

In [25]:
ptf.Default(dataset_path="./gender/", model_name="resnet18", freeze_base_network=True, num_epochs=4)

Dataset Details
    Train path:     ./gender/
    Val path:       None
    CSV train path: None
    CSV val path:  None

Dataset Params
    Input Size:  224
    Batch Size:  4
    Data Shuffle: True
    Processors:   2
    Train-val split:   0.7

Pre-Composed Train Transforms
[{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]

Pre-Composed Val Transforms
[{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]

Dataset Numbers
    Num train images: 14669
    Num val images:   6288
    Num classes:      2

Model Params
    Model name:           resnet18
    Use Gpu:              True
    Use pretrained:       True
    Freeze base network:  True

Model Details
    Loading pretrained model


Downloading: "https://download.pytorch.org/models/resnet18-5c106cde.pth" to /root/.cache/torch/checkpoints/resnet18-5c106cde.pth
100%|██████████| 44.7M/44.7M [00:01<00:00, 46.1MB/s]


    Model Loaded on device
        Model name:           resnet18
        Num layers in model:  31
        Num trainable layers: 1

Optimizer
    Name:          sgd
    Learning rate: 0.01
    Params:        {'lr': 0.01, 'dampening': 0, 'nesterov': False, 'weight_decay': 0, 'momentum': 0}

Learning rate scheduler
    Name:   reduceonplateaulr
    Params: {'mode': 'min', 'factor': 0.1, 'patience': 1, 'verbose': True, 'threshold': 0.0001, 'threshold_mode': 'rel', 'cooldown': 0, 'min_lr': 0, 'epsilon': 1e-08}

Loss
    Name:          softmaxcrossentropy
    Params:        {'weight': None, 'size_average': None, 'ignore_index': -100, 'reduce': None, 'reduction': 'mean'}

Training params
    Num Epochs: 4

Display params
    Display progress:          True
    Display progress realtime: True
    Save Training logs:        True
    Save Intermediate models:  True
    Intermediate model prefix: intermediate_model_



In [26]:
ptf.Summary()



Experiment Summary

System
    Project Name:    Gender_Classification
    Project Dir:     workspace/Gender_Classification/
    Experiment Name: exp-1
    Experiment Dir:  workspace/Gender_Classification/exp-1/
    Library:         Pytorch
    Origin:          ['New', 'New']

Dataset
    Status:       True
    Dataset Type: train
    Train path:   ./gender/
    Val path:     None
    Test path:    False
    CSV Train:    None
    CSV Val:      None
    CSV Test:     False

Dataset Parameters:
    Input Size:   224
    Batch Size:   4
    Shuffle:      True
    Processors:   2
    Num Classes:  2

Dataset Transforms:
    Train transforms: [{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]
    Val transforms:   [{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]
    Test transforms:  [{'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225

#### Break and Resume training

In [0]:
#ptf = prototype(verbose=1);
#ptf.Prototype("Gender_Classification", "exp-1", resume_train=True);

#### Train

In [0]:
ptf.Train()

  0%|          | 0/3668 [00:00<?, ?it/s]

Training Start
    Epoch 1/4
    ----------


100%|█████████▉| 1570/1572 [00:33<00:00, 49.71it/s]

  0%|          | 0/3668 [00:00<?, ?it/s]



    curr_lr - 0.01
    [Epoch 1] Train-acc: 0.926, Train-loss: 0.203 | Val-acc: 0.970420, Val-loss: 0.082, | time: 116.0 sec

    Epoch 2/4
    ----------




  0%|          | 1/3668 [00:00<09:00,  6.78it/s]

  0%|          | 6/3668 [00:00<06:44,  9.06it/s]

  0%|          | 11/3668 [00:00<05:06, 11.92it/s]

  0%|          | 16/3668 [00:00<03:58, 15.34it/s]

  1%|          | 21/3668 [00:00<03:09, 19.26it/s]

  1%|          | 26/3668 [00:00<02:37, 23.08it/s]

  1%|          | 31/3668 [00:00<02:16, 26.73it/s]

  1%|          | 36/3668 [00:00<01:58, 30.55it/s]

  1%|          | 41/3668 [00:01<01:46, 33.96it/s]

  1%|▏         | 46/3668 [00:01<01:38, 36.95it/s]

  1%|▏         | 51/3668 [00:01<01:31, 39.33it/s]

  2%|▏         | 56/3668 [00:01<01:27, 41.35it/s]

  2%|▏         | 61/3668 [00:01<01:27, 41.44it/s]

  2%|▏         | 66/3668 [00:01<01:25, 42.26it/s]

  2%|▏         | 71/3668 [00:01<01:23, 42.87it/s]

  2%|▏         | 76/3668 [00:01<01:21, 43.84it/s]

  2%|▏         | 81/3668 [00:01<01:21, 44.06it/s]

  2%|▏         | 86/3668 [00:02<01:20, 44.61it/s]

  2%|▏         | 91/3668 [00:02<01:18, 45.43it/s]

  3%|▎         | 96/3668 [00:02

#### Zip and download workspace

In [0]:
#!zip -r workspace.zip workspace

  adding: workspace/ (stored 0%)
  adding: workspace/comparison/ (stored 0%)
  adding: workspace/Gender_Classification/ (stored 0%)
  adding: workspace/Gender_Classification/exp-1/ (stored 0%)
  adding: workspace/Gender_Classification/exp-1/output/ (stored 0%)
  adding: workspace/Gender_Classification/exp-1/output/logs/ (stored 0%)
  adding: workspace/Gender_Classification/exp-1/output/logs/train_val_accuracy.png (deflated 9%)
  adding: workspace/Gender_Classification/exp-1/output/logs/train_acc_history.npy (deflated 59%)
  adding: workspace/Gender_Classification/exp-1/output/logs/train_loss_history.npy (deflated 36%)
  adding: workspace/Gender_Classification/exp-1/output/logs/val_loss_history.npy (deflated 36%)
  adding: workspace/Gender_Classification/exp-1/output/logs/train_val_loss.png (deflated 10%)
  adding: workspace/Gender_Classification/exp-1/output/logs/val_acc_history.npy (deflated 60%)
  adding: workspace/Gender_Classification/exp-1/output/models/ (stored 0%)
  adding: work

In [0]:
#from google.colab import files
#files.download("workspace.zip")

KeyboardInterrupt: ignored

## Age Classification Male

#### Create Experiment

In [0]:
ptf = prototype(verbose=1);
ptf.Prototype("Age_Classification", "male2");

Pytorch Version: 1.3.0+cu100

Experiment Details
    Project: Age_Classification
    Experiment: male2
    Dir: /content/workspace/Age_Classification/male2/



In [0]:
ptf.Default(dataset_path="./age/male/", model_name="densenet169", freeze_base_network=True, num_epochs=5)

Dataset Details
    Train path:     ./age/male/
    Val path:       None
    CSV train path: None
    CSV val path:  None

Dataset Params
    Input Size:  224
    Batch Size:  4
    Data Shuffle: True
    Processors:   2
    Train-val split:   0.7

Pre-Composed Train Transforms
[{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]

Pre-Composed Val Transforms
[{'RandomHorizontalFlip': {'p': 0.8}}, {'Normalize': {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}}]

Dataset Numbers
    Num train images: 13173
    Num val images:   5646
    Num classes:      12

Model Params
    Model name:           densenet169
    Use Gpu:              True
    Use pretrained:       True
    Freeze base network:  True

Model Details
    Loading pretrained model


#### Train

In [0]:
%%capture
ptf.Train()

## Age Classification Female

#### Create Experiment

In [0]:
ptf = prototype(verbose=1);
ptf.Prototype("Age_Classification", "female");

Pytorch Version: 1.3.0+cu100

Experiment Details
    Project: Age_Classification
    Experiment: female
    Dir: /content/workspace/Age_Classification/female/



In [0]:
ptf.Default(dataset_path="./age/male/", model_name="resnet18", freeze_base_network=True, num_epochs=5)

#### Train

In [0]:
ptf.Train()

## Inference

#### Get the image

In [0]:
import requests
test_url = "https://i2-prod.mirror.co.uk/incoming/article10883649.ece/ALTERNATES/s615b/PROD-Idris-Elba.jpg"

# URL of the image to be downloaded is defined as image_url 
r = requests.get(test_url) # create HTTP response object 
with open('test.jpg','wb') as f: 
    f.write(r.content) 

#### Set experiment to Inference

In [0]:
ptf.Prototype("Gender_Classification", "exp-1", eval_infer=True);

Model Details
    Loading model - /content/workspace/Gender_Classification/exp-1/output/models/final
    Model loaded!

Experiment Details
    Project: Gender_Classification
    Experiment: exp-1
    Dir: /content/workspace/Gender_Classification/exp-1/



#### Run predictions

In [0]:
img_name = "test.jpg";
predictions = ptf.Infer(img_name=img_name, return_raw=True);
print(predictions)

Prediction
    Image name:         test.jpg
    Predicted class:      male
    Predicted score:      1.3685108423233032

{'img_name': 'test.jpg', 'predicted_class': 'male', 'score': 1.3685108, 'raw': array([-1.2447795,  1.3685108], dtype=float32)}
